# Configuration language

The Terraform configuration language is designed to describe the infrastructure. This page considers the details and properties of different blocks.

## Terraform

The `terraform` block allows specifies the configuration of the application.

There are special block for defining providers.

Check more in the [terraform block reference](https://developer.hashicorp.com/terraform/language/block/terraform).

### Providers

The `required_providers` block inside `terraform` allows you to specify the set of providers to be used in this configuration.

---

The following code adds a random provider to the terraform configuration. And usses it's `random_id` resource to ouput a random value.

In [ ]:
rm -rf /tmp/terraform
mkdir /tmp/terraform
cat << EOF > /tmp/terraform/main.tf
terraform {
  required_providers {
    random = {source = "hashicorp/random"}
  }
}

resource "random_id" "rand_val" {
  byte_length = 8
}

output "variable_output" {
  value = random_id.rand_val.id
}
EOF
cd /tmp/terraform
terraform init &> /dev/null

The output of this terraform configuration is shown in the following cell

In [15]:
terraform output

variable_output = "O3XBEnZXo0I"


## Resource

The `resource` block defines a piece of infrastructure. Pieces of infrastructure really depends on the used provider, but there are common arguments. The generally syntax is following:

```terraform
resource "<TYPE>" "<LABEL>" {
  <PROVIDER_ARGUMENTS>
  <COMMON_ARGUMENTS>
}
```

You have to define the type of resource in the `TYPE` field. The awailable types are defined by the choosen provider.

Check more in [resource block reference](https://developer.hashicorp.com/terraform/language/block/resource).

---

The following cell applies the configuration tha defines the highly specific Nginx Docker image as the resouce.

In [1]:
rm -rf /tmp/terraform
mkdir /tmp/terraform
cat << EOF > /tmp/terraform/main.tf
terraform {
  required_providers {
    docker = {
      source = "kreuzwerker/docker"
      version = "~> 3.0.1"
    }
  }
}

resource "docker_image" "nginx" {
  name = "nginx:1.29.3-alpine3.22-perl"
  keep_locally = true
}
EOF
cd /tmp/terraform
terraform init &> /dev/null
terraform apply -auto-approve &> /dev/null

The specified Docker image appears in Docker runtime.

In [9]:
docker images | grep --color=None "1.29.3-alpine3.22-perl"

nginx                                                1.29.3-alpine3.22-perl       86f721376853   11 hours ago   91.2MB


## Output

The output block can be useful for experimentation purposes, as it allows you to easily print values to stdout.

Check the [output block reference](https://developer.hashicorp.com/terraform/language/block/output).

---

The definition of the `"hello_world` output is shown in the following cell.

In [ ]:
rm -rf /tmp/terraform
mkdir /tmp/terraform
cat << EOF > /tmp/terraform/main.tf
output "hello_world" {
  value = "Hello, stdout!"
}
EOF
cd /tmp/terraform
terraform init &> /dev/null

In such a case, the `terraform apply` will have an `Outputs` section containing the relevant infromation.

In [ ]:
terraform apply -auto-approve


Changes to Outputs:
  + hello_world = "Hello, stdout!"

You can apply this plan to save these new output values to the Terraform state,
without changing any real infrastructure.

Apply complete! Resources: 0 added, 0 changed, 0 destroyed.

Outputs:

hello_world = "Hello, stdout!"


You can also use the `terraform output` command to simply push the outputs to stdout.

In [ ]:
terraform output

hello_world = "Hello, stdout!"


## Variables

The `variable` allows you to define the variables that can be set using an external configuration. This allows you to parameterise you configuration.

---

The following cell adds the `variable` parameter and prints its value alongside the output.

In [ ]:
rm -rf /tmp/terraform
mkdir /tmp/terraform
cat << EOF > /tmp/terraform/main.tf
variable "variable" {
  description = "Value of the name for the Docker container"
  type        = string
  default     = "the value of the variable"
}

output "variable_output" {
  value = var.variable
}
EOF
cd /tmp/terraform
terraform init &> /dev/null

The following cell invokes the configuration output.

In [ ]:
terraform output

variable_output = "the value of the variable"


Pass the value you like your configuration to run with to the `terraform apply` command with `-var` parameter.

In [ ]:
terraform apply -auto-approve -var "variable=custom value"


Changes to Outputs:
  ~ variable_output = "the value of the variable" -> "custom value"

You can apply this plan to save these new output values to the Terraform state,
without changing any real infrastructure.

Apply complete! Resources: 0 added, 0 changed, 0 destroyed.

Outputs:

variable_output = "custom value"
